In [ ]:
import os
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from scipy.ndimage import label
from tqdm import tqdm
import matplotlib.pyplot as plt

MAX_STEPS = 10

# List of desired ratios of parameters to training samples
target_ratios = [0.2, 0.5, 1]

# Ensure output directories exist
def ensure_dir(path):
    os.makedirs(path, exist_ok=True)

def generate_percolation_lattice(size, p):
    return np.random.choice([0, 1], (size, size), p=[1-p, p]).astype(np.uint8)

def check_percolation(lattice):
    labeled, _ = label(lattice)
    top = set(labeled[0]) - {0}
    bottom = set(labeled[-1]) - {0}
    left = set(labeled[:,0]) - {0}
    right = set(labeled[:,-1]) - {0}
    return float(bool(top & bottom) or bool(left & right))

def first_coarse_graining(binary_lattice, dim):
    t = torch.tensor(binary_lattice, dtype=torch.float32).unsqueeze(0).unsqueeze(0)
    patches = F.unfold(t, kernel_size=dim, stride=dim)
    patches = patches.permute(0, 2, 1)
    coarse_vals = patches.mean(dim=2)
    H, W = binary_lattice.shape
    new_h, new_w = H // dim, W // dim
    return coarse_vals.view(1, 1, new_h, new_w).squeeze(0)

class PercolationModel(nn.Module):
    def __init__(self, dim):
        super().__init__()
        self.dim = dim
        self.rule = nn.Sequential(
            nn.Linear(dim * dim, 64),
            nn.ReLU(),
            nn.Linear(64, 1),
            nn.Sigmoid()
        )

    def forward(self, x, max_steps=MAX_STEPS):
        b, c, H, W = x.shape
        for _ in range(max_steps):
            if H < self.dim or W < self.dim:
                break
            patches = F.unfold(x, kernel_size=self.dim, stride=self.dim)
            patches = patches.permute(0, 2, 1).contiguous()
            out = self.rule(patches.view(-1, self.dim*self.dim))
            new_h, new_w = H // self.dim, W // self.dim
            x = out.view(b, 1, new_h, new_w)
            _, _, H, W = x.shape
        return x.squeeze(1).view(b, -1)

def prepare_dataset(N, sizes):
    data = []
    half = int(N/2)
    for _ in tqdm(range(half), desc="Generating uniform data"):
        p = np.random.uniform(0, 1)
        size = np.random.choice(sizes)
        L = generate_percolation_lattice(size, p)
        data.append((L, check_percolation(L)))
    for _ in tqdm(range(half), desc="Generating critical data"):
        p = np.random.uniform(0.55, 0.65)
        size = np.random.choice(sizes)
        L = generate_percolation_lattice(size, p)
        data.append((L, check_percolation(L)))
    return data

def train_epoch(model, device, data, batch_size, opt, crit):
    model.train()
    total_loss = 0.0
    for i in tqdm(range(0, len(data), batch_size), desc="Training"):
        batch = data[i:i+batch_size]
        groups = {}
        for x, y in batch:
            cg = first_coarse_graining(x, DIM)
            size = cg.shape[-2:]
            groups.setdefault(size, []).append((cg, y))
        for group in groups.values():
            lattices, labels = zip(*group)
            inputs = torch.stack(lattices).to(device)
            targets = torch.tensor(labels, dtype=torch.float32, device=device)
            opt.zero_grad()
            outputs = model(inputs)
            loss = crit(outputs.view(-1), targets)
            loss.backward()
            opt.step()
            total_loss += loss.item() * len(group)
    return total_loss / len(data)

def compute_loss(model, device, data, crit):
    model.eval()
    total_loss = 0.0
    with torch.no_grad():
        for x, y in data:
            cg = first_coarse_graining(x, DIM)
            inp = cg.unsqueeze(0).to(device)
            tgt = torch.tensor([y], dtype=torch.float32, device=device)
            out = model(inp)
            loss = crit(out.view(-1), tgt)
            total_loss += loss.item()
    return total_loss / len(data)

def run_experiment(base, epochs, param_ratio):
    global DIM
    DIM = base
    SIZES = [base**2, base**3, base**4]

    # Setup directory structure
    out_dir = f"results/base_{base}"
    ensure_dir(out_dir)

    # Initialize model and compute parameter count
    model = PercolationModel(DIM).to(DEVICE)
    num_params = sum(p.numel() for p in model.parameters() if p.requires_grad)
    train_samples = int(num_params / param_ratio)
    test_samples = train_samples  # Set test samples equal to training samples
    
    print(f"Base={base}, Ratio={param_ratio}: params={num_params}, samples={train_samples}")

    train_data = prepare_dataset(train_samples, SIZES)
    test_data = prepare_dataset(test_samples, SIZES)

    opt = optim.Adam(model.parameters(), lr=1e-3/2, weight_decay=1e-4)
    crit = nn.BCELoss()
    train_losses, test_losses = [], []

    for epoch in range(1, epochs+1):
        tr_loss = train_epoch(model, DEVICE, train_data, batch_size=100, opt=opt, crit=crit)
        te_loss = compute_loss(model, DEVICE, test_data, crit)
        train_losses.append(tr_loss)
        test_losses.append(te_loss)
        print(f"Epoch {epoch}/{epochs} - Train Loss: {tr_loss:.4f}, Test Loss: {te_loss:.4f}")

    # Plot and save
    plt.figure(figsize=(10, 6))
    x = range(1, epochs+1)
    plt.plot(x, train_losses, 'b-o', label='Training Loss')
    plt.plot(x, test_losses, 'g--s', label='Test Loss')
    plt.xlabel('Epochs', fontsize=14)
    plt.ylabel('BCE Loss', fontsize=14)
    plt.title(f'Percolation Loss (base {base}, ratio {param_ratio})', fontsize=16)
    plt.legend()
    plt.tight_layout()
    
    filepath = os.path.join(out_dir, f"loss_ratio{str(param_ratio).replace('.', '_')}.png")
    plt.savefig(filepath)
    plt.close()

if __name__ == "__main__":
    DEVICE = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    bases = [3, 4, 5]
    epochs = 1250
    
    # Create base directories first
    for base in bases:
        ensure_dir(f"results/base_{base}")
    
    # Run experiments
    for ratio in target_ratios:
        for base in bases:
            run_experiment(base, epochs, ratio)

Base=3, Ratio=0.2: params=705, samples=3525


Training: 100%|█████████████████████████████████████████████████████████████████████████████████████| 36/36 [00:00<00:00, 67.65it/s]


Epoch 1/1250 - Train Loss: 0.6738, Test Loss: 0.6763


Training: 100%|█████████████████████████████████████████████████████████████████████████████████████| 36/36 [00:00<00:00, 69.34it/s]


Epoch 2/1250 - Train Loss: 0.6708, Test Loss: 0.6758


...

Training: 100%|█████████████████████████████████████████████████████████████████████████████████████| 18/18 [00:01<00:00, 13.79it/s]


Epoch 476/1250 - Train Loss: 0.1385, Test Loss: 0.1580


Training: 100%|█████████████████████████████████████████████████████████████████████████████████████| 18/18 [00:01<00:00, 14.04it/s]


Epoch 477/1250 - Train Loss: 0.1395, Test Loss: 0.1580


Training:  56%|███████████████████████████████████████████████▏                                     | 10/18 [00:00<00:00, 12.21it/s]

In [ ]:
import os
import time
import platform

# Wait for 1 minute (60 seconds)
print("Notebook execution completed. System will shut down in 1 minute...")
time.sleep(60)

# Determine the operating system
current_os = platform.system()

# Execute the appropriate shutdown command based on the OS
if current_os == "Windows":
    os.system("shutdown /s /t 0")
elif current_os == "Linux" or current_os == "Darwin":  # Darwin is macOS
    os.system("shutdown -h now")
else:
    print(f"Unsupported operating system: {current_os}")
